In [1]:
import math

def findGCD(seq):
    gcd = seq[0]
    for i in range(1,len(seq)):
        gcd=math.gcd(gcd, seq[i])
    return gcd

In [2]:
def findSignature(seq):
    nonzero_seq = [d for d in seq if d!=0]
    if len(nonzero_seq)==0:
        return seq
    sign = 1 if nonzero_seq[0]>0 else -1
    gcd = findGCD(seq)
    return [sign*x//gcd for x in seq]

In [3]:
def findDerivative(seq):
    return [0] if len(seq)<=1 else [seq[i]-seq[i-1] for i in range(1,len(seq))]

In [4]:
def addAll(seq, node, list):
    if 'value' in node:
        list.append( ( seq, node['value'] ) )
    for key in node:
        if key != 'value':
            addAll(seq + [key], node[key], list)

In [5]:
class prefixTree:
    def __init__(self):
        self.data={}
        self.puts=0
        self.nodes=0
    
    def put(self, seq, value):
        node=self.data
        nodeCreated=False
        for i in range(0,len(seq)):
            item=seq[i]
            if not item in node:
                node[item]={}
                if 'value' in node:
                    del node['value']
                self.nodes+=1
                nodeCreated=True
            node=node[item]
        if nodeCreated:
            node['value']=value
            self.puts+=1
        elif 'value' in node:
            node['value']=max(node['value'], value)
    
    def prefix(self, seq):
        list=[]
        node=self.data
        for i in range(0,len(seq)):
            item=seq[i]
            if item in node:
                node=node[item]
            else:
                return list
        addAll(seq, node, list)
        return list
    
    def hasPrefix(self, seq):
        node=self.data
        for i in range(0,len(seq)):
            item=seq[i]
            if item in node:
                node=node[item]
            else:
                return False
        return True

In [6]:
from functools import reduce
next_elm = []

def findNext(seq, trie):
    while True:
        nonZeroIndex =-1
        for i in range(0,len(seq)):
            if seq[i] != 0: 
                nonZeroIndex = i
                break
        if nonZeroIndex < 0:
            return 0
        signature = findSignature(seq)
        list = trie.prefix( signature )
        list = filter(lambda x: len(x[0])>len(signature), list)
        item = next(list, None)
        if item != None:
            best = reduce(lambda a, b: a if a[1]>b[1] else b if b[1]>a[1] else a if len(b[0])<=len(a[0]) else b, list, item)
            nextElement = best[0][len(seq)]
            nextElement *= seq[nonZeroIndex]//signature[nonZeroIndex]
            return nextElement
        if len(seq) <= 3: 
            break
        seq = seq[1:]
    return None

def findNextAndDerive(seq, trie):
    nextElement=findNext(seq, trie)
    if nextElement==None:
        der=findDerivative(seq)
        if len(der)<=3:
            return None
        nextElement=findNextAndDerive(der, trie)
        if nextElement==None:
            return None
        return seq[len(seq)-1]+nextElement
    return nextElement

In [7]:
##### import datasets #####

import pandas as pd

#train_df= pd.read_csv('./data/train.csv', index_col="Id", nrows=100)
test_df = pd.read_csv('../input/test.csv', index_col="Id")
train_df= pd.read_csv('../input/train.csv', index_col="Id")

train_df = train_df['Sequence'].to_dict()
test_df = test_df['Sequence'].to_dict()
#seq_train = {0: [1 for x in range(0,400)]}
seq_train = {}
seq_test = {}
#seq_test = {0: [1 for x in range(0,400)]}

for key in train_df:
    seq1 = train_df[key]
    seq1 = [int(x) for x in seq1.split(',')]
    seq_train[key] = seq1

for key in test_df:
    seq2 = test_df[key]
    seq2 = [int(x) for x in seq2.split(',')]
    seq_test[key] = seq2
    
### our data is dict ###

In [8]:
## for train datasets
trieTrain = prefixTree()
if True:
    for id in seq_train:
        der_train = seq_train[id]
        for derAttempts in range(4):
            train_seq = der_train
            firstInTrie = False
            for subseqAttempts in range(4-derAttempts):
                while len(train_seq)>0 and train_seq[0] == 0:
                    train_seq = train_seq[1:]
                signature = findSignature(train_seq)
                if trieTrain.hasPrefix( signature ):
                    if subseqAttempts == 0:
                        firstInTrie = True
                    break
                trieTrain.put( signature, len(train_seq)*100//len(der_train) )#задаем веса для каждого узла len(train_seq)*100//len(der_train)
                if len(train_seq) <= 3:
                    break
                train_seq = train_seq[1:]
            if firstInTrie:
                break
            der_train = findDerivative(der_train)

In [9]:
def prediction(sequence,trie):
    idx = []
    prediction = []
    for id in sequence:
        der = list(map(int, train_df[id].split(',')))
        next_elm = findNextAndDerive(der, trie)
        if next_elm == None:
            prediction.append(0)
            idx.append(id)
        else:
            prediction.append(next_elm)
            idx.append(id)
    return idx, prediction


In [10]:
idx, prediction = prediction(train_df,trieTrain)

In [24]:
for index in range(len(idx)):
    print('Id:', idx[index], 'prediction:', prediction[index])

Id: 3 prediction: 0
Id: 7 prediction: 0
Id: 8 prediction: 2621440
Id: 11 prediction: 0
Id: 13 prediction: 3167221297608348623853211
Id: 15 prediction: 25
Id: 16 prediction: 0
Id: 18 prediction: 0
Id: 20 prediction: 0
Id: 21 prediction: 0
Id: 23 prediction: 0
Id: 24 prediction: 0
Id: 26 prediction: 9
Id: 28 prediction: 0
Id: 34 prediction: 0
Id: 35 prediction: 908
Id: 36 prediction: 0
Id: 40 prediction: 0
Id: 41 prediction: 510
Id: 44 prediction: 10
Id: 46 prediction: 0
Id: 49 prediction: 0
Id: 51 prediction: 0
Id: 52 prediction: 7964
Id: 53 prediction: 0
Id: 57 prediction: 89
Id: 59 prediction: 0
Id: 61 prediction: 0
Id: 63 prediction: 0
Id: 64 prediction: 0
Id: 65 prediction: 0
Id: 66 prediction: 0
Id: 67 prediction: 0
Id: 69 prediction: 0
Id: 72 prediction: 1342810
Id: 73 prediction: 0
Id: 75 prediction: 0
Id: 76 prediction: 1073741766
Id: 77 prediction: 14
Id: 82 prediction: 0
Id: 86 prediction: 0
Id: 89 prediction: 832966693180608098
Id: 91 prediction: 12494651387941
Id: 92 predict

Id: 738 prediction: 0
Id: 744 prediction: 0
Id: 746 prediction: 6
Id: 747 prediction: 62
Id: 750 prediction: 0
Id: 756 prediction: 0
Id: 759 prediction: 0
Id: 764 prediction: 0
Id: 766 prediction: 1659
Id: 770 prediction: 0
Id: 771 prediction: 0
Id: 775 prediction: 0
Id: 776 prediction: 0
Id: 777 prediction: 0
Id: 780 prediction: 0
Id: 784 prediction: 0
Id: 785 prediction: 0
Id: 786 prediction: 0
Id: 789 prediction: 13
Id: 790 prediction: 44
Id: 792 prediction: 0
Id: 793 prediction: 0
Id: 794 prediction: 19
Id: 796 prediction: 0
Id: 797 prediction: 1339
Id: 801 prediction: 0
Id: 803 prediction: 1732
Id: 804 prediction: 0
Id: 805 prediction: 0
Id: 807 prediction: 0
Id: 809 prediction: 0
Id: 810 prediction: 10059470
Id: 813 prediction: 0
Id: 816 prediction: 0
Id: 817 prediction: 5
Id: 820 prediction: 2686
Id: 823 prediction: 0
Id: 824 prediction: 4
Id: 826 prediction: 0
Id: 827 prediction: 0
Id: 828 prediction: 1814400
Id: 829 prediction: 0
Id: 830 prediction: 0
Id: 831 prediction: 0
Id:

Id: 1634 prediction: 7
Id: 1635 prediction: 0
Id: 1636 prediction: 157
Id: 1639 prediction: 0
Id: 1640 prediction: 0
Id: 1641 prediction: 102
Id: 1642 prediction: 137499
Id: 1644 prediction: 32669300067140567040
Id: 1649 prediction: 0
Id: 1651 prediction: 0
Id: 1656 prediction: 0
Id: 1658 prediction: 0
Id: 1659 prediction: 1200
Id: 1660 prediction: 445480469
Id: 1664 prediction: 0
Id: 1665 prediction: 0
Id: 1666 prediction: 0
Id: 1667 prediction: 0
Id: 1669 prediction: 0
Id: 1671 prediction: 301
Id: 1673 prediction: 2
Id: 1676 prediction: 3
Id: 1679 prediction: 0
Id: 1682 prediction: 5
Id: 1683 prediction: 351843720888320
Id: 1689 prediction: 1
Id: 1690 prediction: 0
Id: 1691 prediction: 1
Id: 1693 prediction: 0
Id: 1694 prediction: 54482152508
Id: 1695 prediction: 0
Id: 1703 prediction: 0
Id: 1704 prediction: 0
Id: 1706 prediction: 0
Id: 1711 prediction: 0
Id: 1712 prediction: 0
Id: 1715 prediction: 1
Id: 1718 prediction: 0
Id: 1719 prediction: 0
Id: 1724 prediction: 0
Id: 1725 predic

Id: 2638 prediction: 0
Id: 2639 prediction: 0
Id: 2640 prediction: 1711
Id: 2648 prediction: 0
Id: 2651 prediction: 0
Id: 2655 prediction: 24
Id: 2656 prediction: 214389
Id: 2659 prediction: 0
Id: 2660 prediction: 0
Id: 2661 prediction: 0
Id: 2662 prediction: 168888
Id: 2667 prediction: 0
Id: 2668 prediction: 0
Id: 2669 prediction: 0
Id: 2674 prediction: 0
Id: 2675 prediction: 0
Id: 2677 prediction: 311112
Id: 2682 prediction: 0
Id: 2683 prediction: 97
Id: 2685 prediction: 2
Id: 2688 prediction: 0
Id: 2690 prediction: 4
Id: 2692 prediction: 0
Id: 2693 prediction: 0
Id: 2695 prediction: 0
Id: 2696 prediction: 0
Id: 2701 prediction: 10294976
Id: 2702 prediction: 170
Id: 2703 prediction: 14
Id: 2705 prediction: 0
Id: 2706 prediction: 30412109306150147954
Id: 2710 prediction: 0
Id: 2712 prediction: 0
Id: 2713 prediction: 0
Id: 2717 prediction: 7199369738058939
Id: 2718 prediction: 0
Id: 2719 prediction: 626
Id: 2720 prediction: 0
Id: 2723 prediction: 1
Id: 2726 prediction: 1270
Id: 2728 pr

Id: 3579 prediction: 0
Id: 3580 prediction: 0
Id: 3581 prediction: 74
Id: 3582 prediction: 45146068753500
Id: 3583 prediction: 0
Id: 3585 prediction: 80
Id: 3586 prediction: 22
Id: 3587 prediction: 45286002241714599985152
Id: 3589 prediction: 0
Id: 3590 prediction: 728
Id: 3594 prediction: 0
Id: 3597 prediction: 7
Id: 3598 prediction: 0
Id: 3599 prediction: 0
Id: 3604 prediction: 0
Id: 3607 prediction: 3
Id: 3612 prediction: 0
Id: 3613 prediction: 0
Id: 3616 prediction: 4
Id: 3620 prediction: 0
Id: 3625 prediction: 0
Id: 3628 prediction: 351690259364115330
Id: 3629 prediction: 3
Id: 3632 prediction: 0
Id: 3634 prediction: 494
Id: 3635 prediction: 0
Id: 3638 prediction: 0
Id: 3640 prediction: 78
Id: 3643 prediction: 0
Id: 3645 prediction: 201
Id: 3647 prediction: 0
Id: 3648 prediction: 2333458
Id: 3649 prediction: 0
Id: 3650 prediction: 0
Id: 3652 prediction: 3474
Id: 3653 prediction: 4073273163776
Id: 3655 prediction: -1162831
Id: 3657 prediction: 223
Id: 3660 prediction: 703921
Id: 36

...

Id: 223407 prediction: 0
Id: 223408 prediction: 0
Id: 223410 prediction: 0
Id: 223411 prediction: 0
Id: 223414 prediction: 0
Id: 223416 prediction: 0
Id: 223417 prediction: 0
Id: 223418 prediction: 75
Id: 223419 prediction: 0
Id: 223421 prediction: 268269270271
Id: 223422 prediction: 0
Id: 223426 prediction: 1353713
Id: 223429 prediction: 21
Id: 223430 prediction: 0
Id: 223431 prediction: 0
Id: 223432 prediction: 0
Id: 223433 prediction: 249
Id: 223435 prediction: 0
Id: 223436 prediction: 0
Id: 223441 prediction: 0
Id: 223443 prediction: 1339805
Id: 223444 prediction: 0
Id: 223445 prediction: 78
Id: 223446 prediction: 0
Id: 223447 prediction: 0
Id: 223448 prediction: 13
Id: 223449 prediction: 15
Id: 223450 prediction: 90
Id: 223452 prediction: 0
Id: 223453 prediction: 0
Id: 223454 prediction: 0
Id: 223458 prediction: 0
Id: 223468 prediction: 0
Id: 223471 prediction: 0
Id: 223472 prediction: 0
Id: 223473 prediction: 0
Id: 223474 prediction: 425
Id: 223475 prediction: 0
Id: 223482 predic

Id: 224388 prediction: 0
Id: 224389 prediction: 0
Id: 224391 prediction: 0
Id: 224395 prediction: 20
Id: 224396 prediction: 6
Id: 224397 prediction: 553
Id: 224398 prediction: 257
Id: 224403 prediction: 0
Id: 224405 prediction: 0
Id: 224407 prediction: 4
Id: 224409 prediction: 0
Id: 224416 prediction: 732
Id: 224417 prediction: 0
Id: 224418 prediction: 7
Id: 224420 prediction: 0
Id: 224423 prediction: 82720755783423343562004
Id: 224424 prediction: 0
Id: 224426 prediction: 2
Id: 224428 prediction: 6
Id: 224430 prediction: 8
Id: 224431 prediction: 0
Id: 224432 prediction: 0
Id: 224433 prediction: 47576320
Id: 224438 prediction: 0
Id: 224440 prediction: 5
Id: 224443 prediction: 615998
Id: 224446 prediction: 0
Id: 224447 prediction: 0
Id: 224449 prediction: 0
Id: 224450 prediction: 0
Id: 224452 prediction: 0
Id: 224453 prediction: 225
Id: 224455 prediction: 0
Id: 224456 prediction: 0
Id: 224458 prediction: 0
Id: 224459 prediction: 66
Id: 224461 prediction: 512
Id: 224464 prediction: 6
Id: 

Id: 225387 prediction: 0
Id: 225388 prediction: 25059
Id: 225389 prediction: 0
Id: 225391 prediction: 217
Id: 225392 prediction: 1483
Id: 225393 prediction: 1
Id: 225395 prediction: 0
Id: 225397 prediction: 0
Id: 225398 prediction: 56
Id: 225399 prediction: 0
Id: 225400 prediction: 746
Id: 225402 prediction: 0
Id: 225404 prediction: 0
Id: 225405 prediction: 9208188955560907491
Id: 225407 prediction: 0
Id: 225408 prediction: 0
Id: 225411 prediction: 2
Id: 225413 prediction: 47
Id: 225415 prediction: 0
Id: 225417 prediction: 280
Id: 225418 prediction: 103
Id: 225419 prediction: 0
Id: 225422 prediction: 6917318875805359573600621821952
Id: 225423 prediction: 0
Id: 225424 prediction: 429455704
Id: 225425 prediction: 0
Id: 225427 prediction: 70
Id: 225428 prediction: 103
Id: 225429 prediction: 0
Id: 225435 prediction: 334
Id: 225438 prediction: 1049041748046875
Id: 225439 prediction: 0
Id: 225440 prediction: 0
Id: 225441 prediction: 1
Id: 225443 prediction: 0
Id: 225444 prediction: 11
Id: 22

Id: 226516 prediction: 0
Id: 226517 prediction: 1225
Id: 226518 prediction: 0
Id: 226519 prediction: 1
Id: 226520 prediction: 0
Id: 226523 prediction: 283
Id: 226524 prediction: 23493
Id: 226527 prediction: 0
Id: 226529 prediction: 1103
Id: 226530 prediction: 166
Id: 226532 prediction: 1279
Id: 226536 prediction: 0
Id: 226539 prediction: 50
Id: 226541 prediction: 0
Id: 226544 prediction: 0
Id: 226547 prediction: 0
Id: 226549 prediction: 233341
Id: 226552 prediction: 40360
Id: 226554 prediction: 0
Id: 226557 prediction: 3324
Id: 226558 prediction: 0
Id: 226563 prediction: 1279
Id: 226567 prediction: 81950
Id: 226568 prediction: 0
Id: 226570 prediction: 105908093453250
Id: 226571 prediction: 127
Id: 226573 prediction: 16
Id: 226574 prediction: 2960
Id: 226575 prediction: 1
Id: 226577 prediction: 149
Id: 226578 prediction: 481
Id: 226579 prediction: 0
Id: 226581 prediction: 129
Id: 226583 prediction: 5016948276247458
Id: 226589 prediction: 119244359152460559009548
Id: 226590 prediction: 0

Id: 227373 prediction: 0
Id: 227376 prediction: 0
Id: 227378 prediction: 129
Id: 227381 prediction: 0
Id: 227387 prediction: 0
Id: 227389 prediction: 6184
Id: 227390 prediction: 0
Id: 227391 prediction: 477
Id: 227396 prediction: 0
Id: 227400 prediction: 0
Id: 227402 prediction: 0
Id: 227404 prediction: 0
Id: 227407 prediction: 0
Id: 227408 prediction: 229
Id: 227410 prediction: 4111419327088961408862781440000000
Id: 227417 prediction: 18
Id: 227419 prediction: 214
Id: 227424 prediction: 0
Id: 227425 prediction: 2980232238769525
Id: 227426 prediction: 0
Id: 227427 prediction: 0
Id: 227428 prediction: 99
Id: 227429 prediction: 731
Id: 227430 prediction: 84
Id: 227431 prediction: 55079
Id: 227433 prediction: 2479
Id: 227434 prediction: 0
Id: 227436 prediction: 65
Id: 227438 prediction: 0
Id: 227439 prediction: 78
Id: 227441 prediction: 6
Id: 227444 prediction: 0
Id: 227446 prediction: 184
Id: 227448 prediction: 37
Id: 227449 prediction: 6893
Id: 227451 prediction: 0
Id: 227456 prediction

In [38]:
null = prediction.count(0)
not_null = len(prediction) - null
null
#not_null

64928

In [37]:
acc = not_null*100//len(prediction)
acc

42